In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
pd.set_option('display.max_columns', None)
import sklearn.decomposition as sk

## Loading and Merging Data

In [4]:
womens_health = pd.read_csv('../health/health.csv')
#gdp_pc = pd.read_csv('../DataShared/API_NY.GDP.PCAP.CD_DS2_en_csv_v2_62/gdp_per_capita.csv', header=2)
econ = pd.read_excel('../DataShared/rep_wb/econ.xlsx')
illness_prevalence = pd.read_excel('../DataShared/rep_ihme_prev/disease_incidence.xlsx')
empowerment = pd.read_excel('../DataShared/rep_swper/womens_empowerment.xlsx')

In [5]:
data = pd.read_excel('../DataShared/rep_gho/data.xlsx')

In [2]:
mmr_data = pd.read_csv('../DataShared/maternal-mortality-ratio-modeled-estimate-per-100-000-live-births/Maternal mortality ratio (modeled estimate, per 100,000 live births).csv')

In [6]:
womens_health_renamed = womens_health.rename(columns={"Country Name" : "setting", "Year" : "date", "Value" : "estimate", "Indicator Name" : "indicator_name", "Country Code" : "iso3"})

In [124]:
len(womens_health_renamed['setting'].unique())

265

In [7]:
mmr_data_renamed = mmr_data.rename(columns={"Country Name" : "setting", "Year" : "date", "Value" : "estimate", "Indicator Name" : "indicator_name", "Country Code" : "iso3"})

In [126]:
len(mmr_data_renamed['setting'].unique())

242

### Exploring

In [7]:
womens_health_indicators = womens_health_renamed['indicator_name'].unique()
(womens_health.shape)

(578360, 6)

In [8]:
womens_health_extracted_features2 = []

for indicator in womens_health_indicators:
    column = womens_health_renamed[womens_health_renamed['indicator_name'] == indicator]
    column = column.rename(columns={'estimate' : indicator})
    womens_health_extracted_features2.append(column[['setting', 'date', indicator]])

In [26]:
womens_merged = pd.merge(womens_health_extracted_features2[0], womens_health_extracted_features2[1], how='outer', on=['setting', 'date'])

for i in range(2, len(womens_health_extracted_features2)):
    womens_merged = pd.merge(womens_merged, womens_health_extracted_features2[i], how='outer', on=['setting', 'date'])

In [31]:
womens_merged.shape

(16936, 200)

In [30]:
womens_merged.isnull().sum().sum()

2774968

## Merging

### Extracting Features

In [7]:
def income_level(data):
    income_level = data[['iso3', 'wbincome2024']]
    income_level.insert(2, "income_num", np.zeros(len(income_level)))
    income_level = income_level.drop_duplicates()

    for i in range(0, len(income_level)):
        if income_level.iloc[i, 1] == 'Low income':
            income_level.iloc[i, 2] = 1

        elif income_level.iloc[i, 1] == 'Lower middle income':
            income_level.iloc[i, 2] = 2

        elif income_level.iloc[i, 1] == 'Upper middle income':
            income_level.iloc[i, 2] = 3

        elif income_level.iloc[i, 1] == 'High income':
            income_level.iloc[i, 2] = 4
    
    return income_level

In [8]:
womens_health_indicators = womens_health_renamed['indicator_name'].unique()
#data_indicators = data['indicator_name'].unique()
illness_prevalence_indicators = illness_prevalence['indicator_name'].unique()
empowerment_indicators = empowerment['indicator_name'].unique()

In [9]:
len(womens_health_indicators)

198

In [10]:
womens_health_extracted_features = []

for indicator in womens_health_indicators:
    if indicator == 'Maternal mortality ratio (modeled estimate, per 100,000 live births)':
        continue
    if indicator == 'Maternal mortality ratio (national estimate, per 100,000 live births)':
        continue

    column = womens_health_renamed[womens_health_renamed['indicator_name'] == indicator]
    column = column.rename(columns={'estimate' : indicator})
    womens_health_extracted_features.append(column[['date', indicator, 'iso3']])

In [11]:
len(womens_health_extracted_features)

196

In [12]:
mmr_indicators = mmr_data_renamed['indicator_name'].unique()
mmr_extracted = []

for indicator in mmr_indicators:
    column = mmr_data_renamed[mmr_data_renamed['indicator_name'] == indicator]
    column = column.rename(columns={'estimate' : indicator})
    womens_health_extracted_features.append(column[['date', indicator, 'iso3']])

In [13]:
illness_prevalence_extracted_features = []

for indicator in illness_prevalence_indicators:
    column = illness_prevalence[illness_prevalence['indicator_name'] == indicator]
    i_f = indicator + ' female'
    col_f = column[column['subgroup'] == 'Female']
    col_f = col_f.rename(columns={'estimate' : i_f})
    
    i_m = indicator + ' male'
    col_m = column[column['subgroup'] == 'Male']
    col_m = col_m.rename(columns={'estimate' : i_m})
    
    illness_prevalence_extracted_features.append(col_f[['date', i_f, 'iso3']])
    illness_prevalence_extracted_features.append(col_m[['date', i_m, 'iso3']])

In [14]:
len(illness_prevalence_extracted_features)

386

In [15]:
empowerment_extracted_features = []

for indicator in empowerment_indicators:
    column = empowerment[empowerment['indicator_name'] == indicator]
    i_q1 = indicator + ' Quintile 1 (poorest)'
    col_q1 = column[column['subgroup'] == 'Quintile 1 (poorest)']
    col_q1 = col_q1.rename(columns={'estimate' : i_q1})

    i_q5 = indicator + ' Quintile 5 (richest)'
    col_q5 = column[column['subgroup'] == 'Quintile 5 (richest)']
    col_q5 = col_q5.rename(columns={'estimate' : i_q5})

    empowerment_extracted_features.append(col_q1[['date', i_q1, 'iso3']])
    empowerment_extracted_features.append(col_q5[['date', i_q5, 'iso3']])

In [16]:
len(empowerment_extracted_features)

18

In [17]:
econ_gender = econ[econ['dimension'] == 'Sex']
econ_indicators_gender = econ_gender['indicator_name'].unique()

econ_wealth = econ[econ['dimension'] == 'Economic status (wealth quintile)']
econ_indicators_wealth = econ_wealth['indicator_name'].unique()

econ_residence = econ[econ['dimension'] == 'Place of residence']
econ_indicators_residence = econ_residence['indicator_name'].unique()

In [18]:
econ_extracted_gender = []

for indicator in econ_indicators_gender:
    column = econ_gender[econ_gender['indicator_name'] == indicator]

    i_f = indicator + ' female'
    col_f = column[column['subgroup'] == 'Female']
    col_f = col_f.rename(columns={'estimate' : i_f})
    
    i_m = indicator + ' male'
    col_m = column[column['subgroup'] == 'Male']
    col_m = col_m.rename(columns={'estimate' : i_m})
    
    econ_extracted_gender.append(col_f[['date', i_f, 'iso3']])
    econ_extracted_gender.append(col_m[['date', i_m, 'iso3']])

econ_extracted_residence = []

for indicator in econ_indicators_residence:
    column = econ_residence[econ_residence['indicator_name'] == indicator]

    i_r = indicator + ' rural'
    col_r = column[column['subgroup'] == 'Rural']
    col_r = col_r.rename(columns={'estimate' : i_r})
    
    i_u = indicator + ' urban'
    col_u = column[column['subgroup'] == 'Urban']
    col_u = col_u.rename(columns={'estimate' : i_u})
    
    econ_extracted_residence.append(col_r[['date', i_r, 'iso3']])
    econ_extracted_residence.append(col_u[['date', i_u, 'iso3']])

econ_extracted_wealth = []

for indicator in econ_indicators_wealth:
    column = econ_wealth[econ_wealth['indicator_name'] == indicator]

    i_q1 = indicator + ' Quintile 1 (poorest)'
    col_q1 = column[column['subgroup'] == 'Quintile 1 (poorest)']
    col_q1 = col_q1.rename(columns={'estimate' : i_q1})
    
    i_q5 = indicator + ' Quintile 5 (richest)'
    col_q5 = column[column['subgroup'] == 'Quintile 5 (richest)']
    col_q5 = col_q5.rename(columns={'estimate' : i_q5})
    
    econ_extracted_wealth.append(col_q1[['date', i_q1, 'iso3']])
    econ_extracted_wealth.append(col_q5[['date', i_q5, 'iso3']])

### Merging Between 1985 and 2018

In [20]:
def merging_data(after, before):

    merged_data = pd.merge(womens_health_extracted_features[0], womens_health_extracted_features[1], how='outer', on=['iso3', 'date'])

    for i in range(2, len(womens_health_extracted_features)):
        merged_data = pd.merge(merged_data, womens_health_extracted_features[i], how='outer', on=['iso3', 'date'])
    
    for i in range(0, len(empowerment_extracted_features)):
        merged_data = pd.merge(merged_data, empowerment_extracted_features[i], how='outer', on=['iso3', 'date'])

    for i in range(0, len(illness_prevalence_extracted_features)):
        merged_data = pd.merge(merged_data, illness_prevalence_extracted_features[i], how='outer', on=['iso3', 'date'])

    for i in range(0, len(econ_extracted_gender)):
        merged_data = pd.merge(merged_data, econ_extracted_gender[i], how='outer', on=['iso3', 'date'])

    for i in range(0, len(econ_extracted_residence)):
        merged_data = pd.merge(merged_data, econ_extracted_residence[i], how='outer', on=['iso3', 'date'])
    
    for i in range(0, len(econ_extracted_wealth)):
        merged_data = pd.merge(merged_data, econ_extracted_wealth[i], how='outer', on=['iso3', 'date'])
    
    for i in range(0, len(mmr_extracted)):
        merged_data = pd.merge(merged_data, mmr_extracted[i], how='outer', on=['iso3', 'date'])

    income_var = income_level(data)
    income_var = income_var[['iso3', 'income_num']]
    merged_data = pd.merge(merged_data, income_var, how='outer', on=['iso3'])

    merged_datasets = merged_data[merged_data['date'] > after]
    merged_datasets = merged_datasets[merged_datasets['date'] < before]

    return merged_datasets

In [21]:
m_withinyears = merging_data(1984, 2019)

: 

In [ ]:
m_withinyears['date'].unique()

array([2019., 2015., 2010., 2000., 2020., 2018., 2017., 2016., 2014.,
       2013., 2012., 2011., 2009., 2008., 2007., 2006., 2005., 2004.,
       2003., 2002., 2001., 1999., 1998., 1997., 1996., 1995., 1994.,
       1993., 1992., 1991., 1990., 1989., 1988., 1987., 1986., 1985.])

In [17]:
iso_setting = womens_health_renamed[['setting', 'iso3']]

In [22]:
iso_setting_dict = {}
for code in womens_health_renamed['iso3'].unique():
    iso_setting_dict[code] = womens_health_renamed[womens_health_renamed['iso3'] == code]['setting'].unique()[0]

In [ ]:
m_withinyears = m_withinyears.reset_index(drop=True)

In [ ]:
m_withinyears[m_withinyears['income_num'] == 0]

date  \
8316  2019.0   
8317  2015.0   
8318  2010.0   
8319  2000.0   
8320  2020.0   
8321  2018.0   
8322  2017.0   
8323  2016.0   
8324  2014.0   
8325  2013.0   
8326  2012.0   
8327  2011.0   
8328  2009.0   
8329  2008.0   
8330  2007.0   
8331  2006.0   
8332  2005.0   
8333  2004.0   
8334  2003.0   
8335  2002.0   
8336  2001.0   
8337  1999.0   
8338  1998.0   
8339  1997.0   
8340  1996.0   
8341  1995.0   
8342  1994.0   
8343  1993.0   
8344  1992.0   
8345  1991.0   
8346  1990.0   
8347  1989.0   
8348  1988.0   
8349  1987.0   
8350  1986.0   
8351  1985.0   
9540  2000.0   
9541  2005.0   
9542  2010.0   
9543  2015.0   
9544  2019.0   
9545  2000.0   
9546  2005.0   
9547  2010.0   
9548  2015.0   
9549  2019.0   

      Women and girls who use menstrual materials (% of women and girls ages 15-49 who had a menstrual period within the last year)  \
8316                                                NaN                                                                               
8317                                                NaN                                                                               
8318                                                NaN                                                                               
8319                                                NaN                                                                               
8320                                                NaN                                                                               
8321                                                NaN                                                                               
8322                                                NaN                                                                               
8323                                                NaN                                                                               
8324                                                NaN                                                                               
8325                                                NaN                                                                               
8326                                                NaN                                                                               
8327                                                NaN                                                                               
8328                                                NaN                                                                               
8329                                                NaN                                                                               
8330                                                NaN                                                                               
8331                                                NaN                                                                               
8332                                                NaN                                                                               
8333                                                NaN                                                                               
8334                                                NaN                                                                               
8335                                                NaN                                                                               
8336                                                NaN                                                                               
8337                                                NaN                                                                               
8338                                                NaN                                                                               
8339           

In [ ]:
for i in range(m_withinyears.shape[0]):
    if m_withinyears.loc[i, 'iso3'] not in iso_setting_dict.keys():
        print(m_withinyears.loc[i, 'iso3'])
        continue
    m_withinyears.loc[i, 'iso3'] = iso_setting_dict[m_withinyears.loc[i, 'iso3']]

COK
COK
COK
COK
COK
NIU
NIU
NIU
NIU
NIU


In [ ]:
m_withinyears.rename(columns={'iso3': 'setting'}, inplace=True)
m_withinyears

date  \
0     2019.0   
1     2015.0   
2     2010.0   
3     2000.0   
4     2020.0   
...      ...   
9545  2000.0   
9546  2005.0   
9547  2010.0   
9548  2015.0   
9549  2019.0   

      Women and girls who use menstrual materials (% of women and girls ages 15-49 who had a menstrual period within the last year)  \
0                                                 94.52                                                                               
1                                                   NaN                                                                               
2                                                   NaN                                                                               
3                                                   NaN                                                                               
4                                                   NaN                                                                               
...                                                 ...                                                                               
9545                                                NaN                                                                               
9546                                                NaN                                                                               
9547                                                NaN                                                                               
9548                                                NaN                                                                               
9549                                                NaN                                                                               

      setting  \
0     Algeria   
1     Algeria   
2     Algeria   
3     Algeria   
4     Algeria   
...       ...   
9545      NIU   
9546      NIU   
9547      NIU   
9548      NIU   
9549      NIU   

      Cause of death, by communicable diseases and maternal, prenatal and nutrition conditions, ages 5-14 (% of population ages 5-14)  \
0                                                16.054                                                                                 
1                                                18.055                                                                                 
2                                                17.537                                                                                 
3                                                20.944                                                                                 
4                                                   NaN                                                                                 
...                                                 ...                                                                                 
9545                                                NaN                                                                                 
9546                                                NaN                                                                                 
9547                                                NaN                                                                                 
9548                                                NaN                                                                                 
9549                                                NaN                                                                                 

      Mortality rate attributed to household and ambient air pollution, age-standardized, female (per 100,000 female population)  \
0                                                  45.0                                                                            
1                                                   NaN                         

### Merging All

In [106]:
def merging_data_all():

    merged_data = pd.merge(womens_health_extracted_features[0], womens_health_extracted_features[1], how='outer', on=['iso3', 'date'])

    for i in range(2, len(womens_health_extracted_features)):
        merged_data = pd.merge(merged_data, womens_health_extracted_features[i], how='outer', on=['iso3', 'date'])
    
    for i in range(0, len(empowerment_extracted_features)):
        merged_data = pd.merge(merged_data, empowerment_extracted_features[i], how='outer', on=['iso3', 'date'])

    for i in range(0, len(illness_prevalence_extracted_features)):
        merged_data = pd.merge(merged_data, illness_prevalence_extracted_features[i], how='outer', on=['iso3', 'date'])

    for i in range(0, len(econ_extracted_gender)):
        merged_data = pd.merge(merged_data, econ_extracted_gender[i], how='outer', on=['iso3', 'date'])

    for i in range(0, len(econ_extracted_residence)):
        merged_data = pd.merge(merged_data, econ_extracted_residence[i], how='outer', on=['iso3', 'date'])
    
    for i in range(0, len(econ_extracted_wealth)):
        merged_data = pd.merge(merged_data, econ_extracted_wealth[i], how='outer', on=['iso3', 'date'])\
        
    for i in range(0, len(mmr_extracted)):
        merged_data = pd.merge(merged_data, mmr_extracted[i], how='outer', on=['iso3', 'date'])
    
    income_var = income_level(data)
    income_var = income_var[['iso3', 'income_num']]
    merged_data = pd.merge(merged_data, income_var, how='outer', on=['iso3'])


    return merged_data

In [107]:
m = merging_data_all()

In [108]:
for i in range(m.shape[0]):
    if m.iloc[i][2] not in iso_setting_dict.keys():
        print(m.iloc[i][2])
        continue
    m.loc[i, 'iso3'] = iso_setting_dict[m.loc[i, 'iso3']]

/var/folders/jd/0gmk2m5x1cl2hh0v_hsx43q40000gn/T/ipykernel_41978/786165030.py:2: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  if m.iloc[i][2] not in iso_setting_dict.keys():


COK
COK
COK
COK
COK
NIU
NIU
NIU
NIU
NIU
TKL


/var/folders/jd/0gmk2m5x1cl2hh0v_hsx43q40000gn/T/ipykernel_41978/786165030.py:3: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  print(m.iloc[i][2])


In [109]:
m.rename(columns={'iso3': 'setting'}, inplace=True)
m

date  \
0      2019.0   
1      2015.0   
2      2010.0   
3      2000.0   
4      2022.0   
...       ...   
16943  2005.0   
16944  2010.0   
16945  2015.0   
16946  2019.0   
16947     NaN   

       Women and girls who use menstrual materials (% of women and girls ages 15-49 who had a menstrual period within the last year)  \
0                                                  94.52                                                                               
1                                                    NaN                                                                               
2                                                    NaN                                                                               
3                                                    NaN                                                                               
4                                                    NaN                                                                               
...                                                  ...                                                                               
16943                                                NaN                                                                               
16944                                                NaN                                                                               
16945                                                NaN                                                                               
16946                                                NaN                                                                               
16947                                                NaN                                                                               

       setting  \
0      Algeria   
1      Algeria   
2      Algeria   
3      Algeria   
4      Algeria   
...        ...   
16943      NIU   
16944      NIU   
16945      NIU   
16946      NIU   
16947      TKL   

       Cause of death, by communicable diseases and maternal, prenatal and nutrition conditions, ages 5-14 (% of population ages 5-14)  \
0                                                 16.054                                                                                 
1                                                 18.055                                                                                 
2                                                 17.537                                                                                 
3                                                 20.944                                                                                 
4                                                    NaN                                                                                 
...                                                  ...                                                                                 
16943                                                NaN                                                                                 
16944                                                NaN                                                                                 
16945                                                NaN                                                                                 
16946                                                NaN                                                                                 
16947                                                NaN                                                                                 

       Mortality rate attributed to household and ambient air pollution, age-standardized, female (per 100,000 female population)  \
0                                                   45.0                                                                            
1                              

In [129]:
m[m['income_num'] == 0]['setting'].unique()

array(['Venezuela, RB', 'COK', 'NIU', 'TKL'], dtype=object)

## Saving Data

In [ ]:
file_path = '/Users/rosalitarosenberg/Library/CloudStorage/OneDrive-AustralianNationalUniversity/Comp Honours/code'

In [110]:
pd.DataFrame(m).to_pickle(file_path + '/raw_merged_data_v2')

In [ ]:
pd.DataFrame(m_withinyears).to_pickle(file_path + '/raw_merged_data_v2_withinyears')